In [2]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/hackhathon-repik-ai/augmented_train_data.csv
/kaggle/input/hackhathon-repik-ai/damage_classification_model.h5
/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images/1573.jpg_aug_8.jpg
/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images/3941.jpg_aug_13.jpg
/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images/7014.jpg_aug_7.jpg
/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images/4805.jpg_aug_1.jpg
/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images/5198.jpg_aug_2.jpg
/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images/846.jpg_aug_13.jpg
/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images/2227.jpg_aug_8.jpg
/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images/2727.jpg_aug_0.jpg
/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images/4877.jpg_aug_4.jpg
/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images/4575.jpg_aug_18.jpg
/kag

In [3]:
import os

# Specify the path to the folder with extracted images
extracted_folder = '/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images'

# Get the list of files in the folder
files = os.listdir(extracted_folder)

# Filter only files with certain image extensions (e.g., '.jpg', '.png', etc.)
image_files = [file for file in files if file.lower().endswith(('.jpg'))] #(('.jpg', '.jpeg', '.png', '.gif'))

# Count the number of image files
num_images = len(image_files)

# Print the result
print(f"Number of images in the folder: {num_images}")

Number of images in the folder: 58422


In [4]:
import pandas as pd
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.applications import VGG16, ResNet50, InceptionV3
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D
from tensorflow.keras.models import Model

# Load CSV file
df = pd.read_csv('/kaggle/input/hackhathon-repik-ai/augmented_train_data.csv')
# Convert integer labels to strings
df['label'] = df['label'].astype(str)

# Split dataset into training and testing sets
train_df, val_df = train_test_split(df, test_size=0.3, random_state=42)

# Create ImageDataGenerator for data augmentation and normalization
datagen = ImageDataGenerator(rescale=1./255,
                             shear_range=0.2,
                             zoom_range=0.2,
                             horizontal_flip=True)

In [5]:
print(df.shape)
print(train_df.shape)
print(val_df.shape)

(58422, 5)
(40895, 5)
(17527, 5)


In [6]:
df.head()

image_id  filename label    damage_type                 image_path
0     6203  6203.jpg     2        scratch  augmented_images\6203.jpg
1     5599  5599.jpg     2        scratch  augmented_images\5599.jpg
2     2235  2235.jpg     5  glass shatter  augmented_images\2235.jpg
3     2858  2858.jpg     4           dent  augmented_images\2858.jpg
4     5589  5589.jpg     4           dent  augmented_images\5589.jpg

In [7]:
df.tail()

image_id             filename label  damage_type  \
58417  3994.jpg   3994.jpg_aug_8.jpg     6  lamp broken   
58418  3994.jpg   3994.jpg_aug_9.jpg     6  lamp broken   
58419  3994.jpg  3994.jpg_aug_10.jpg     6  lamp broken   
58420  3994.jpg  3994.jpg_aug_11.jpg     6  lamp broken   
58421  3994.jpg  3994.jpg_aug_12.jpg     6  lamp broken   

                                 image_path  
58417   augmented_images/3994.jpg_aug_8.jpg  
58418   augmented_images/3994.jpg_aug_9.jpg  
58419  augmented_images/3994.jpg_aug_10.jpg  
58420  augmented_images/3994.jpg_aug_11.jpg  
58421  augmented_images/3994.jpg_aug_12.jpg

In [8]:
img_directory = '/kaggle/input/hackhathon-repik-ai/augmented_images/augmented_images'
# Check the first few rows of train_df and val_df
print("Train DataFrame:")
print(train_df.head())

print("\nValidation DataFrame:")
print(val_df.head())

# Verify existence of image files in the directory
import os

for filename in train_df['filename']:
    filepath = os.path.join(img_directory, filename)
    if not os.path.exists(filepath):
        print(f"File not found: {filepath}")

for filename in val_df['filename']:
    filepath = os.path.join(img_directory, filename)
    if not os.path.exists(filepath):
        print(f"File not found: {filepath}")


Train DataFrame:
       image_id             filename label  damage_type  \
30878  1890.jpg  1890.jpg_aug_45.jpg     1        crack   
49333  5265.jpg  5265.jpg_aug_11.jpg     6  lamp broken   
57084   713.jpg    713.jpg_aug_1.jpg     6  lamp broken   
55302  7093.jpg   7093.jpg_aug_0.jpg     6  lamp broken   
6493   3642.jpg   3642.jpg_aug_1.jpg     2      scratch   

                                 image_path  
30878  augmented_images/1890.jpg_aug_45.jpg  
49333  augmented_images/5265.jpg_aug_11.jpg  
57084    augmented_images/713.jpg_aug_1.jpg  
55302   augmented_images/7093.jpg_aug_0.jpg  
6493    augmented_images/3642.jpg_aug_1.jpg  

Validation DataFrame:
       image_id             filename label  damage_type  \
11032  3976.jpg   3976.jpg_aug_0.jpg     2      scratch   
5396       2209             2209.jpg     4         dent   
57935   434.jpg    434.jpg_aug_7.jpg     6  lamp broken   
43942   443.jpg    443.jpg_aug_0.jpg     3    tire flat   
39018  3522.jpg  3522.jpg_aug_20.j

In [9]:
# Create data generators
img_size = (200, 200)  # VGG16 input size
batch_size = 32
train_generator = datagen.flow_from_dataframe(dataframe=train_df,
                                              directory=img_directory,
                                              x_col='filename', y_col='label',
                                              class_mode='categorical',
                                              target_size=img_size,
                                              batch_size=batch_size)

val_generator = datagen.flow_from_dataframe(dataframe=val_df,
                                            directory=img_directory,
                                            x_col='filename',
                                            y_col='label',
                                            class_mode='categorical',
                                            target_size=img_size,
                                            batch_size=batch_size)

Found 40895 validated image filenames belonging to 6 classes.
Found 17527 validated image filenames belonging to 6 classes.


In [10]:
df[['label','damage_type']].value_counts()

label  damage_type  
4      dent             9978
6      lamp broken      9884
1      crack            9864
3      tire flat        9821
5      glass shatter    9480
2      scratch          9395
Name: count, dtype: int64

# ResNet50

In [11]:
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D, Dropout
from tensorflow.keras.optimizers import RMSprop
from tensorflow.keras.callbacks import LearningRateScheduler, EarlyStopping
from tensorflow.keras.models import Model
from tensorflow.keras.applications import ResNet50
from tensorflow.keras.applications.resnet import preprocess_input

# ResNet50
base_model_resnet = ResNet50(weights='imagenet', include_top=False, input_shape=(224, 224, 3))
x = base_model_resnet.output
x = GlobalAveragePooling2D()(x)
x = Dense(256, activation='relu')(x)
x = Dropout(0.5)(x)  # Add dropout for regularization
predictions_resnet = Dense(6, activation='softmax')(x)
model_resnet = Model(inputs=base_model_resnet.input, outputs=predictions_resnet)

# Compile the model
model_resnet.compile(optimizer=RMSprop(learning_rate=1e-4), loss='categorical_crossentropy', metrics=['accuracy'])

# Learning rate scheduler
def lr_scheduler(epoch, lr):
    return lr * 0.9  # Adjust the factor as needed

learning_rate_scheduler = LearningRateScheduler(lr_scheduler)

# Early stopping
early_stopping = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)

# Train ResNet50
model_resnet.fit(train_generator, epochs=10, validation_data=val_generator, callbacks=[learning_rate_scheduler, early_stopping])

# Evaluate ResNet50
eval_result_resnet = model_resnet.evaluate(val_generator)
print(f"ResNet50 Test Accuracy: {eval_result_resnet[1]*100:.2f}%")


94765736/94765736 [==============================] - 1s 0us/step
Epoch 1/10
1278/1278 [==============================] - 1059s 801ms/step - loss: 0.3519 - accuracy: 0.8802 - val_loss: 0.4080 - val_accuracy: 0.9192 - lr: 9.0000e-05
Epoch 2/10
1278/1278 [==============================] - 723s 566ms/step - loss: 0.1192 - accuracy: 0.9630 - val_loss: 0.2215 - val_accuracy: 0.9648 - lr: 8.1000e-05
Epoch 3/10
1278/1278 [==============================] - 715s 560ms/step - loss: 0.0692 - accuracy: 0.9781 - val_loss: 0.1861 - val_accuracy: 0.9603 - lr: 7.2900e-05
Epoch 4/10
1278/1278 [==============================] - 729s 570ms/step - loss: 0.0417 - accuracy: 0.9870 - val_loss: 0.1934 - val_accuracy: 0.9624 - lr: 6.5610e-05
Epoch 5/10
1278/1278 [==============================] - 708s 554ms/step - loss: 0.0326 - accuracy: 0.9907 - val_loss: 0.0585 - val_accuracy: 0.9876 - lr: 5.9049e-05
Epoch 6/10
1278/1278 [==============================] - 704s 551ms/step - loss: 0.0224 - accuracy: 0.9934 - v

In [12]:
# Save the model
model_resnet.save('model_resnet.h5')


/opt/conda/lib/python3.10/site-packages/keras/src/engine/training.py:3000: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


# MobileNetV2

In [14]:
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D, Dropout
from tensorflow.keras.optimizers import RMSprop
from tensorflow.keras.callbacks import LearningRateScheduler, EarlyStopping
from tensorflow.keras.models import Model
from tensorflow.keras.applications import MobileNetV2

# MobileNetV2
base_model_mobilenet = MobileNetV2(weights='imagenet', include_top=False, input_shape=(224, 224, 3))
x = base_model_mobilenet.output
x = GlobalAveragePooling2D()(x)
x = Dense(256, activation='relu')(x)
x = Dropout(0.5)(x)  # Add dropout for regularization
predictions_mobilenet = Dense(6, activation='softmax')(x)
model_mobilenet = Model(inputs=base_model_mobilenet.input, outputs=predictions_mobilenet)

# Compile the model
model_mobilenet.compile(optimizer=RMSprop(learning_rate=1e-4), loss='categorical_crossentropy', metrics=['accuracy'])

# Learning rate scheduler
def lr_scheduler(epoch, lr):
    return lr * 0.9  # Adjust the factor as needed

learning_rate_scheduler = LearningRateScheduler(lr_scheduler)

# Early stopping
early_stopping = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)

# Train MobileNetV2
model_mobilenet.fit(train_generator, epochs=10, validation_data=val_generator, callbacks=[learning_rate_scheduler, early_stopping])

# Evaluate MobileNetV2
eval_result_mobilenet = model_mobilenet.evaluate(val_generator)
print(f"MobileNetV2 Test Accuracy: {eval_result_mobilenet[1]*100:.2f}%")

9406464/9406464 [==============================] - 0s 0us/step
Epoch 1/10
1278/1278 [==============================] - 763s 581ms/step - loss: 0.4872 - accuracy: 0.8182 - val_loss: 0.5031 - val_accuracy: 0.8586 - lr: 9.0000e-05
Epoch 2/10
1278/1278 [==============================] - 738s 578ms/step - loss: 0.1525 - accuracy: 0.9468 - val_loss: 0.2167 - val_accuracy: 0.9455 - lr: 8.1000e-05
Epoch 3/10
1278/1278 [==============================] - 713s 558ms/step - loss: 0.0830 - accuracy: 0.9721 - val_loss: 0.0674 - val_accuracy: 0.9798 - lr: 7.2900e-05
Epoch 4/10
1278/1278 [==============================] - 740s 579ms/step - loss: 0.0535 - accuracy: 0.9826 - val_loss: 0.0607 - val_accuracy: 0.9835 - lr: 6.5610e-05
Epoch 5/10
1278/1278 [==============================] - 720s 563ms/step - loss: 0.0383 - accuracy: 0.9883 - val_loss: 0.0519 - val_accuracy: 0.9865 - lr: 5.9049e-05
Epoch 6/10
1278/1278 [==============================] - 705s 552ms/step - loss: 0.0330 - accuracy: 0.9906 - val_

In [16]:
# Save the model
model_mobilenet.save('model_mobilenet.h5')